In [1]:
from nupack import *
# This is poor practice, I know
import pandas as pd
import openpyxl
import RNA
import subprocess
import ghostscript
import matplotlib.pyplot as plt
from collections import OrderedDict
from operator import getitem
import scipy

salmonella_16s = "AGAGTTTGATCATGGCTCAGATTGAACGCTGGCGGCAGGCCTAACACATGCAAGTCGAACGGTAACAGGAAGCAGCTTGCTGCTTTGCTGACGAGTGGCGGACGGGTGAGTAATGTCTGGGAAACTGCCTGATGGAGGGGGATAACTACTGGAAACGGTGGCTAATACCGCATAACGTCGCAAGACCAAAGAGGGGGACCTTCGGGCCTCTTGCCATCAGATGTGCCCAGATGGGATTAGCTTGTTGGTGAGGTAACGGCTCACCAAGGCGACGATCCCTAGCTGGTCTGAGAGGATGACCAGCCACACTGGAACTGAGACACGGTCCAGACTCCTACGGGAGGCAGCAGTGGGGAATATTGCACAATGGGCGCAAGCCTGATGCAGCCATGCCGCGTGTATGAAGAAGGCCTTCGGGTTGTAAAGTACTTTCAGCGGGGAGGAAGGTGTTGTGGTTAATAACCGCAGCAATTGACGTTACCCGCAGAAGAAGCACCGGCTAACTCCGTGCCAGCAGCCGCGGTAATACGGAGGGTGCAAGCGTTAATCGGAATTACTGGGCGTAAAGCGCACGCAGGCGGTCTGTCAAGTCGGATGTGAAATCCCCGGGCTCAACCTGGGAACTGCATTCGAAACTGGCAGGCTTGAGTCTTGTAGAGGGGGGTAGAATTCCAGGTGTAGCGGTGAAATGCGTAGAGATCTGGAGGAATACCGGTGGCGAAGGCGGCCCCCTGGACAAAGACTGACGCTCAGGTGCGAAAGCGTGGGGAGCAAACAGGATTAGATACCCTGGTAGTCCACGCCGTAAACGATGTCTACTTGGAGGTTGTGCCCTTGAGGCGTGGCTTCCGGAGCTAACGCGTTAAGTAGACCGCCTGGGGAGTACGGCCGCAAGGTTAAAACTCAAATGAATTGACGGGGGCCCGCACAAGCGGTGGAGCATGTGGTTTAATTCGATGCAACGCGAAGAACCTTACCTGGTCTTGACATCCACAGAACTTTCCAGAGATGGATTGGTGCCTTCGGGAACTGTGAGACAGGTGCTGCATGGCTGTCGTCAGCTCGTGTTGTGAAATGTTGGGTTAAGTCCCGCAACGAGCGCAACCCTTATCCTTTGTTGCCAGCGGTCCGGCCGGGAACTCAAAGGAGACTGCCAGTGATAAACTGGAGGAAGGTGGGGATGACGTCAAGTCATCATGGCCCTTACGACCAGGGCTACACACGTGCTACAATGGCGCATACAAAGAGAAGCGACCTCGCGAGAGCAAGCGGACCTCATAAAGTGCGTCGTAGTCCGGATTGGAGTCTGCAACTCGACTCCATGAAGTCGGAATCGCTAGTAATCGTGGATCAGAATGCCACGGTGAATACGTTCCCGGGCCTTGTACACACCGCCCGTCACACCATGGGAGTGGGTTGCAAAAGAAGTAGGTAGCTTAACCTTCGGGGGGGCGCTTACCACTTTGTGATTCATGACTGGGGTGAAGTCGTAACAAGGTAACCGTAGGGGAACCTGCGGTTGGATCACCTCCTT" 

conserved_hairpin_sequence = "GGACUUUAGAACAGAGGAGAUAAAGAUG"
linker = "AACCUGGCGGCAGCGCAAAAG"

# Targeting Series B toehold
# toehold size = 36 nt
# Alpha toehold size = 25
# Betta toehold size = 11

toehold_window = 36

In [2]:
salmonella_16s_rna = salmonella_16s.replace("T", "U")

In [3]:
def screen_rna(rna:str, toehold_window):
    struct_mfe_container = {}
    stop_codons = ["UGA", "UAG", "UAA"]
    fail_list = []
    succeed_list = []
    outer_defect_dict = {}
    rna = rna.replace("T", "U")
    for i in range(len(rna)):
    # for i in range(30):
        if i + toehold_window < len(rna):
            trigger_strand = Strand(rna[i:i+toehold_window], name="trigger")
            toehold_strand = Strand(str(~trigger_strand), name="toehold")
            toehold_betta_compliment = ~Strand(str(toehold_strand)[-11:], name="~ toehold betta")
            check_stop = any(stop in str(toehold_betta_compliment) for stop in stop_codons)
            if not check_stop:
                try:
                    # Creating domains:
                    trigger_domain = Domain(str(trigger_strand), name="trigger domain")
                    toehold_domain = Domain(str(toehold_strand), name="toehold domain")
                    hairpin_domain = Domain(conserved_hairpin_sequence, name="hairpin")
                    toehold_betta_compliment_domain = Domain(str(toehold_betta_compliment), name="toehold betta compliment domain")
                    linker_domain = Domain(linker, name="linker domain")

                    # Creating Target Strands:
                    switch_target_strand = TargetStrand([toehold_domain, hairpin_domain, toehold_betta_compliment_domain, linker_domain], name="Switch Target Strand")
                    switch_target_strand_str = toehold_domain.__str__() + hairpin_domain.__str__() + toehold_betta_compliment_domain.__str__() + linker_domain.__str__()

                    trigger_target_strand = TargetStrand([trigger_domain], name="Trigger Target Strand")
                    trigger_target_strand_str = trigger_domain.__str__()
                

                    struct_mfe_hybrid = RNA.cofold(switch_target_strand_str + "&" + trigger_target_strand_str)
                    struct_mfe_switch = RNA.fold(switch_target_strand_str)


                    container = {}
                    container["Index"] = i 
                    # container["Switch"] = switch_target_strand_str
                    container["Trigger"] = trigger_target_strand_str
                    container["Switch Structure"] = struct_mfe_switch[0]
                    container["Switch Self-Folding Energy"] = struct_mfe_switch[1]
                    container["Switch and Trigger Hybrid Structure"] = struct_mfe_hybrid[0]
                    container["Switch and Trigger Hybrid Folding Energy"] = struct_mfe_hybrid[1]
                    container["Ratio Hybrid / Switch"] = struct_mfe_hybrid[1] / struct_mfe_switch[1]
                    

                    # Creating Complexes:
                    switch_complex = TargetComplex([switch_target_strand], ".25(11.3(5.12)5.3)11.21", name="Switch Complex")
                    trigger_complex = TargetComplex([trigger_target_strand], ".36", name="Trigger Complex")
                    switch_trigger_complex = TargetComplex([trigger_target_strand, switch_target_strand], "(36+)36.60") # .3(5.12)5.3)11.21

                    # Creating Tubes:
                    Tube1 = TargetTube(on_targets={switch_complex:1e-8, trigger_complex:1e-8, switch_trigger_complex: 1e-8}, name='Tube1',  off_targets=SetSpec(max_size=3, include=[], exclude=[]))
                    my_model = Model()
                    my_tubes = [Tube1]
                    my_design = tube_design(tubes=my_tubes,
                        hard_constraints=[], soft_constraints=[],
                        defect_weights=None, options=None, model=my_model)   

                    # Running Tube
                    results = my_design.run(trials=1)[0]

                    # Adding defect rates to dictionary
                    container[results.defects.complexes.to_numpy()[0][0] + " Defect Nominal"] = results.defects.complexes.to_numpy()[0][1]
                    container[results.defects.complexes.to_numpy()[0][0] + " Defect Normalized"] = results.defects.complexes.to_numpy()[0][2]
                    container["Hybrid Defect Nominal"] = results.defects.complexes.to_numpy()[1][1]
                    container["Hybrid Defect Normalized"] = results.defects.complexes.to_numpy()[1][2]
                    container[results.defects.complexes.to_numpy()[2][0] + " Defect Nominal"] = results.defects.complexes.to_numpy()[2][1]
                    container[results.defects.complexes.to_numpy()[2][0] + " Defect Normalized"] = results.defects.complexes.to_numpy()[2][2]
                    
                    succeed_list.append(switch_target_strand_str)
                    struct_mfe_container[switch_target_strand_str] = container
                except:
                    # print(str(switch_target_strand_str) + " failed")
                    fail_list.append(str(trigger_strand))
    print("Suceeded: ", len(succeed_list))
    print("Failed: ", len(fail_list))
    return struct_mfe_container, outer_defect_dict               


struct, defect_dict = screen_rna(salmonella_16s, toehold_window)

'Index', 'Trigger', 'Switch Structure', 'Switch Self-Folding Energy', 'Switch and Trigger Hybrid Structure', 'Switch and Trigger Hybrid Energy', 'Trigger Complex Defect Nominal', 'Trigger Complex Defect Normalized', 'Hybrid Defect Nominal', 'Hybrid Defect Normalized', 'Switch Complex Defect Nominal', 'Switch Complex Defect Normalized', 'Ratio Hybrid / Switch'

In [120]:
# Sorted by Switch Complex Defect Nominal
switch_nominal_list = []

sorted_struct = sorted(struct, key=lambda x: (struct[x]["Switch Complex Defect Nominal"]))
for i in sorted_struct:
    # print(struct[i]["Switch Complex Defect Nominal"], i)
    switch_nominal_list.append(struct[i]["Switch Complex Defect Nominal"])

In [121]:
# Sorted by Trigger Defect Nominal
trigger_nominal_list = []

sorted_struct = sorted(struct, key=lambda x: (struct[x]["Trigger Complex Defect Nominal"]))
for i in sorted_struct:
    # print(struct[i]["Trigger Complex Defect Nominal"], i)
    trigger_nominal_list.append(struct[i]["Trigger Complex Defect Nominal"])

In [122]:
# Sorted by Hybrid Complex Defect Nominal
hybrid_nominal_list = []

sorted_struct = sorted(struct, key=lambda x: (struct[x]["Hybrid Defect Nominal"]))
for i in sorted_struct:
    # print(struct[i]["Hybrid Defect Nominal"], i)
    hybrid_nominal_list.append(struct[i]["Hybrid Defect Nominal"])

In [123]:
# Sorted by Switch Self-Folding Energy
sorted_struct = sorted(struct, key=lambda x: (struct[x]["Switch Self-Folding Energy"]))
for i in sorted_struct:
    # print(struct[i]["Switch Self-Folding Energy"], i)
    pass

In [124]:
# Sorted by Ratio
sorted_struct = sorted(struct, key=lambda x: (struct[x]["Ratio Hybrid / Switch"]), reverse=True)
for i in sorted_struct:
    print(struct[i]["Ratio Hybrid / Switch"], i)


3.702439098823361 UUAACCACAACACCUUCCUCCCCGCUGAAAGUACUUGGACUUUAGAACAGAGGAGAUAAAGAUGAAGUACUUUCAAACCUGGCGGCAGCGCAAAAG
3.5756303026096856 CCCCCCUCUACAAGACUCAAGCCUGCCAGUUUCGAAGGACUUUAGAACAGAGGAGAUAAAGAUGUUCGAAACUGGAACCUGGCGGCAGCGCAAAAG
3.506726440522966 UCCCGAAGGCACCAAUCCAUCUCUGGAAAGUUCUGUGGACUUUAGAACAGAGGAGAUAAAGAUGACAGAACUUUCAACCUGGCGGCAGCGCAAAAG
3.4409089521928267 UAACCACAACACCUUCCUCCCCGCUGAAAGUACUUUGGACUUUAGAACAGAGGAGAUAAAGAUGAAAGUACUUUCAACCUGGCGGCAGCGCAAAAG
3.4235295314414826 UACCCCCCUCUACAAGACUCAAGCCUGCCAGUUUCGGGACUUUAGAACAGAGGAGAUAAAGAUGCGAAACUGGCAAACCUGGCGGCAGCGCAAAAG
3.4043479587720786 CCCCCCCGAAGGUUAAGCUACCUACUUCUUUUGCAAGGACUUUAGAACAGAGGAGAUAAAGAUGUUGCAAAAGAAAACCUGGCGGCAGCGCAAAAG
3.3856503400469156 AUUAACCACAACACCUUCCUCCCCGCUGAAAGUACUGGACUUUAGAACAGAGGAGAUAAAGAUGAGUACUUUCAGAACCUGGCGGCAGCGCAAAAG
3.3583332697550454 CCCGAAGGCACCAAUCCAUCUCUGGAAAGUUCUGUGGGACUUUAGAACAGAGGAGAUAAAGAUGCACAGAACUUUAACCUGGCGGCAGCGCAAAAG
3.357143028872932 CCCCCUCUACAAGACUCAAGCCUGCCAGUUUCGAAUGGACUUUAGAACAGAGGAGA

In [125]:
for x in struct:
    struct[x]["Switch Defect Nominal Percentile"] = int(scipy.stats.percentileofscore(switch_nominal_list, struct[x]["Switch Complex Defect Nominal"]))
    struct[x]["Trigger Defect Nominal Percentile"] = int(scipy.stats.percentileofscore(trigger_nominal_list, struct[x]["Trigger Complex Defect Nominal"]))
    struct[x]["Hybrid Defect Nominal Percentile"] = int(scipy.stats.percentileofscore(hybrid_nominal_list, struct[x]["Hybrid Defect Nominal"]))

In [126]:
#Sort by textbook algorithm

for x in struct:
    struct[x]["Algorithm Score"] = 5 * struct[x]["Trigger Complex Defect Nominal"] + 4 * struct[x]["Switch Complex Defect Nominal"]

In [127]:
# Sorted by Ratio
sorted_struct = sorted(struct, key=lambda x: (struct[x]["Algorithm Score"]))
for i in sorted_struct:
    print(struct[i]["Algorithm Score"], i)

109.60066379517238 GACUUAACCCAACAUUUCACAACACGAGCUGACGACGGACUUUAGAACAGAGGAGAUAAAGAUGGUCGUCAGCUCAACCUGGCGGCAGCGCAAAAG
110.06588912744074 ACUUAACCCAACAUUUCACAACACGAGCUGACGACAGGACUUUAGAACAGAGGAGAUAAAGAUGUGUCGUCAGCUAACCUGGCGGCAGCGCAAAAG
111.81212219184071 CUUAACCCAACAUUUCACAACACGAGCUGACGACAGGGACUUUAGAACAGAGGAGAUAAAGAUGCUGUCGUCAGCAACCUGGCGGCAGCGCAAAAG
115.23275662552452 UUCCAGUAGUUAUCCCCCUCCAUCAGGCAGUUUCCCGGACUUUAGAACAGAGGAGAUAAAGAUGGGGAAACUGCCAACCUGGCGGCAGCGCAAAAG
115.33410986136295 UAUUAACCACAACACCUUCCUCCCCGCUGAAAGUACGGACUUUAGAACAGAGGAGAUAAAGAUGGUACUUUCAGCAACCUGGCGGCAGCGCAAAAG
115.61798678837954 UUUCCAGUAGUUAUCCCCCUCCAUCAGGCAGUUUCCGGACUUUAGAACAGAGGAGAUAAAGAUGGGAAACUGCCUAACCUGGCGGCAGCGCAAAAG
116.24284822001295 UUCUACCCCCCUCUACAAGACUCAAGCCUGCCAGUUGGACUUUAGAACAGAGGAGAUAAAGAUGAACUGGCAGGCAACCUGGCGGCAGCGCAAAAG
117.30049345707525 UCUACCCCCCUCUACAAGACUCAAGCCUGCCAGUUUGGACUUUAGAACAGAGGAGAUAAAGAUGAAACUGGCAGGAACCUGGCGGCAGCGCAAAAG
117.39978050900814 AUUCUACCCCCCUCUACAAGACUCAAGCCUGCCAGUGGACUUUAGAACAGAGG

In [128]:
top_three = ["UUAACCACAACACCUUCCUCCCCGCUGAAAGUACUUGGACUUUAGAACAGAGGAGAUAAAGAUGAAGUACUUUCAAACCUGGCGGCAGCGCAAAAG","CCCCCCUCUACAAGACUCAAGCCUGCCAGUUUCGAAGGACUUUAGAACAGAGGAGAUAAAGAUGUUCGAAACUGGAACCUGGCGGCAGCGCAAAAG", 
"GACUUAACCCAACAUUUCACAACACGAGCUGACGACGGACUUUAGAACAGAGGAGAUAAAGAUGGUCGUCAGCUCAACCUGGCGGCAGCGCAAAAG"]

for i in top_three:
    print(struct[i])

{'Index': 423, 'Trigger': 'AAGUACUUUCAGCGGGGAGGAAGGUGUUGUGGUUAA', 'Switch Structure': '.....................(((((((((((((((.(.(((((............))))).).))))))))))......)))))...........', 'Switch Self-Folding Energy': -20.5, 'Switch and Trigger Hybrid Structure': '.(((((((((((((((((((((((((((((((((((..............(((....((((........))))....))).(((....))).....))))))))))))))))))))))))))))))))))).', 'Switch and Trigger Hybrid Folding Energy': -75.9000015258789, 'Ratio Hybrid / Switch': 3.702439098823361, 'Trigger Complex Defect Nominal': 15.955622174508125, 'Trigger Complex Defect Normalized': 0.44321172706967016, 'Hybrid Defect Nominal': 23.748439113024222, 'Hybrid Defect Normalized': 0.17991241752291076, 'Switch Complex Defect Nominal': 13.751592226969793, 'Switch Complex Defect Normalized': 0.14324575236426867, 'Switch Defect Nominal Percentile': 3, 'Trigger Defect Nominal Percentile': 56, 'Hybrid Defect Nominal Percentile': 42, 'Algorithm Score': 134.7844797804198}
{'Index': 628, 'Trigg

In [129]:
# testing against close relatives of S. enterica.

ecoli = "AGAGUUUGAUCAUGGCUCAGAUUGAACGCUGGCGGCAGGCCUAACACAUGCAAGUCGAACGGUAACAGGAAGAAGCUUGCUCUUUGCUGACGAGUGGCGGACGGGUGAGUAAUGUCUGGGAAACUGCCUGAUGGAGGGGGAUAACUACUGGAAACGGUAGCUAAUACCGCAUAACGUCGCAAGACCAAAGAGGGGGACCUUCGGGCCUCUUGCCAUCGGAUGUGCCCAGAUGGGAUUAGCUAGUAGGUGGGGUAACGGCUCACCUAGGCGACGAUCCCUAGCUGGUCUGAGAGGAUGACCAGCCACACUGGAACUGAGACACGGUCCAGACUCCUACGGGAGGCAGCAGUGGGGAAUAUUGCACAAUGGGCGCAAGCCUGAUGCAGCCAUGCCGCGUGUAUGAAGAAGGCCUUCGGGUUGUAAAGUACUUUCAGCGGGGAGGAAGGGAGUAAAGUUAAUACCUUUGCUCAUUGACGUUACCCGCAGAAGAAGCACCGGCUAACUCCGUGCCAGCAGCCGCGGUAAUACGGAGGGUGCAAGCGUUAAUCGGAAUUACUGGGCGUAAAGCGCACGCAGGCGGUUUGUUAAGUCAGAUGUGAAAUCCCCGGGCUCAACCUGGGAACUGCAUCUGAUACUGGCAAGCUUGAGUCUCGUAGAGGGGGGUAGAAUUCCAGGUGUAGCGGUGAAAUGCGUAGAGAUCUGGAGGAAUACCGGUGGCGAAGGCGGCCCCCUGGACGAAGACUGACGCUCAGGUGCGAAAGCGUGGGGAGCAAACAGGAUUAGAUACCCUGGUAGUCCACGCCGUAAACGAUGUCGACUUGGAGGUUGUGCCCUUGAGGCGUGGCUUCCGGAGCUAACGCGUUAAGUCGACCGCCUGGGGAGUACGGCCGCAAGGUUAAAACUCAAAUGAAUUGACGGGGGCCCGCACAAGCGGUGGAGCAUGUGGUUUAAUUCGAUGCAACGCGAAGAACCUUACCUGGUCUUGACAUCCACGGAAGUUUUCAGAGAUGAGAAUGUGCCUUCGGGAACCGUGAGACAGGUGCUGCAUGGCUGUCGUCAGCUCGUGUUGUGAAAUGUUGGGUUAAGUCCCGCAACGAGCGCAACCCUUAUCCUUUGUUGCCAGCGGUCCGGCCGGGAACUCAAAGGAGACUGCCAGUGAUAAACUGGAGGAAGGUGGGGAUGACGUCAAGUCAUCAUGGCCCUUACGACCAGGGCUACACACGUGCUACAAUGGCGCAUACAAAGAGAAGCGACCUCGCGAGAGCAAGCGGACCUCAUAAAGUGCGUCGUAGUCCGGAUUGGAGUCUGCAACUCGACUCCAUGAAGUCGGAAUCGCUAGUAAUCGUGGAUCAGAAUGCCACGGUGAAUACGUUCCCGGGCCUUGUACACACCGCCCGUCACACCAUGGGAGUGGGUUGCAAAAGAAGUAGGUAGCUUAACCUUCGGGAGGGCGCUUACCACUUUGUGAUUCAUGACUGGGGUGAAGUCGUAACAAGGUAACCGUAGGGGAACCUGCGGUUG"

sboydii = "UAGAGUUUGAUCAUGGCUCAGAUUGAACGCUGGCGGCAGGCCUAACACAUGCAAGUCGAACGGUAACAGGAAUCAGCUUGCUGAUUCGCUGACGAGUGGCGGACGGGUGAGUAAUGUCUGGGAAACUGCCUGAUGGAGGGGGAUAACUACUGGAAACGGUAGCUAAUACCGCAUAAUGUCGCAAGACCAAAGAGGGGGACCUUCGGGCCUCUUGCCAUCGGAUGUGCCCAGAUGGGAUUAGCUUGUUGGUGGGGUAACGGCUCACCAAGGCGACGAUCCCUAGCUGGUCUGAGAGGAUGACCAGCCACACUGGAACUGAGACACGGUCCAGACUCCUACGGGAGGCAGCAGUGGGGAAUAUUGCACAAUGGGCGCAAGCCUGAUGCAGCCAUGCCGCGUGUAUGAAGAAGGCCUUCGGGUUGUAAAGUACUUUCAGCGGGGAGGAAGGGAGUAAAGUUAAUACCUUUGCUCAUUGACGUUAUCCGCAGAAGAAGCACCGGCUAACUCCGUGCCAGCAGCCGCGGUAAUACGGAGGGUGCAAGCGUUAAUCGGAAUUACUGGGCGUAAAGCGCACGCAGGCGGUUUGUUAAGUCAGAUGUGAAAUCCCCGGGCUCAACCUGGGAACUGCAUCUGAUACUGGCAAGCUUGAGUCUCGUAGAGGGGGGUAGAAUUCCAGGUGUAGCGGUGAAAUGCGUAGAGAUCUGGAGGAAUACCGGUGGCGAAGGCGGCCCCCUGGACGAAGACUGACGCUCAGGUGCGAAAGCGUGGGGAGCAAACAGGAUUAGAUACCCUGGUAGUCCACGCCGUAAACGAUGUCGACUUGGAGGUUGUGCCCUUGAGGCGUGGCUUCCGGAGCUAACGCGUUAAGUCGACCGCCUGGGGAGUACGGCCGCAAGGUUAAAACUCAAAUGAAUUGACGGGGGCCCGCACAAGCGGUGGAGCAUGUGGUUUAAUUCGAUGCAACGCGAAGAACCUUACCUGGUCUUGACAUCCACGGAAGUUUUCAGAGAUGAGAAUGUGCCUUCGGGAACCGUGAGACAGGUGCUGCAUGGCUGUCGUCAGCUCGUGUUGUGAAAUGUUGGGUUAAGUCCCGCAACGAGCGCAACCCUUAUCCUUUGUUGCCAGCGGUCCGGCCGGGAACUCAAAGGAGACUGCCAGUGAUAAACUGGAGGAAGGUGGGGACGACGUCAAGUCAUCAUGGCCCUUACGACCAGGGCUACACACGUGCUACAAUGGCGCAUACAAAGAGAAGCGACCUCGCGAGAGCAAGCGGACCUCAUAAAGUGCGUCGUAGUCCGGAUUGGAGUCUGCAACUCGACUCCAUGAAGUCGGAAUCGCUAGUAAUCGUGGAUCAGAAUGCCACGGUGAAUACGUUCCCGGGCCUUGUACACACCGCCCGUCACACCAUGGGAGUGGGUUGCAAAAGAAGUAGGUAGCUUAACCUUCGGGAGGGCGCUUACCACUUUGUGAUUCAUGACUGGGGUGAAGU"

sdysenteriae = "UGGCUCAGAUUGAACGCUGGCGGCAGGCCUAACACAUGCAAGUCGAACGGUAACAGAAAGCAGCUUGCUGUUUGCUGACGAGUGGCGGACGGGUGAGUAAUGUCUGGGAAACUGCCUGAUGGAGGGGGAUAACUACUGGAAACGGUAGCUAAUACCGCAUAACGUCGCAAGACCAAAGAGGGGGACCUUCGGGCCUCUUGCCAUCGGAUGUGCCCAGAUGGGAUUAGCUAGUAGGUGGGGUAACGGCUCACCUAGGCGACGAUCCCUAGCUGGUCUGAGAGGAUGACCAGCCACACUGGAACUGAGACACGGUCCAGACUCCUACGGGAGGCAGCAGUGGGGAAUAUUGCACAAUGGGCGCAAGCCUGAUGCAGCCAUGCCGCGUGUAUGAAGAAGGCCUUCGGGUUGUAAAGUACUUUCAGCGGGGAGGAAGGGAGUAAAGUUAAUACCUUUGCUCAUUGACGUUACCCGCAGAAGAAGCACCGGCUAACUCCGUGCCAGCAGCCGCGGUAAUACGGAGGGUGCAAGCGUUAAUCGGAAUUACUGGGCGUAAAGCGCACGCAGGCGGUUUGUUAAGUCAGAUGUGAAAUCCCCGGGCUCAACCUGGGAACUGCAUCUGAUACUGGCAAGCUUGAGUCUCGUAGAGGGGGGUAGAAUUCCAGGUGUAGCGGUGAAAUGCGUAGAGAUCUGGAGGAAUACCGGUGGCGAAGGCGGCCCCCUGGACGAAAACUGACGCUCAGGUGCGAAAGCGUGGGGAGCAAACAGGAUUAGAUACCCUGGUAGUCCACGCCGUAAACGAUGUCGACUUGGAGGUUGUGCCCUUGAGGCGUGGCUUCCGGAGCUAACGCGUUAAGUCGACCGCCUGGGGAGUACGGCCGCAAGGUUAAAACUCAAAUGAAUUGACGGGGGCCCGCACAAGCGGUGGAGCAUGUGGUUUAAUUCGAUGCAACGCGAAGAACCUUACCUGGUCUUGACAUCCACAGAACCUUGUAGAGAUACGAGGGUGCCUUCGGGAACUGUGAGACAGGUGCUGCAUGGCUGUCGUCAGCUCGUGUUGUGAAAUGUUGGGUUAAGUCCCGCAACGAGCGCAACCCUUAUCCUUUGUUGCCAGCGGUCCGGCCGGGAACUCAAAGGAGACUGCCAGUGAUAAACUGGAGGAAGGUGGGGAUGACGUCAAGUCAUCAUGGCCCUUACGACCAGGGCUACACACGUGCUACAAUGGCGCAUACAAAGAGAAGCGACCUCGCGAGAGCAAGCGGACCUCAUAAAGUGCGUCGUAGUCCGGAUUGGAGUCUGCAACUCGACUCCAUGAAGUCGGAAUCGCUAGUAAUCGUGGAUCAGAAUGUCACGGUGAAUACGUUCCCGGGCCUUGUACACACCGCCCGUCACACCAUGGGAGUGGGUUGCAAAAGAAGUAGGUAGCUUAACCUUCGGGAGGGCGCUUACCACUUUGUGAUUCAUGACUGGGGUGAAGUCGUAACAAGGUA"

In [130]:
new_struct = struct.copy()

In [131]:
def calc_binding(struct):
    strains = [salmonella_16s_rna, ecoli, sboydii, sdysenteriae]
    strain_names = ["salmonella_16s_rna", "ecoli", "sboydii", "sdysenteriae"]
    for i in struct:
        for bact in range(len(strains)):
            print(bact)
            print(strain_names[bact])
            concat = i + "&" + strains[bact]
            proc = subprocess.Popen("RNAup -b -d2 --noLP -c S", stdin=subprocess.PIPE, stdout=subprocess.PIPE, shell=True)
            coms = proc.communicate(bytes(concat, "utf-8"))[0]
            split_coms = str(coms).split(":")
            split_coms = split_coms[1].split("(")
            split_coms = split_coms[1].split("=")
            tfe = split_coms[0]
            print("TFE: ", tfe)
            struct[i]["Total free energy of binding W/ " + strain_names[bact]] = float(tfe)
            print(struct[i])


calc_binding(new_struct)

0
salmonella_16s_rna
TFE:  -23.23 
{'Index': 7, 'Trigger': 'GAUCAUGGCUCAGAUUGAACGCUGGCGGCAGGCCUA', 'Switch Structure': '...((((((((((((.((......((((((((((((.(.(((((............))))).).)))))))))))))))))))))))).)).....', 'Switch Self-Folding Energy': -48.5, 'Switch and Trigger Hybrid Structure': '((((((((((((((((((((((((((((((((((((...........(((..(((.....((....))....)))...)))(((....))).....))))))))))))))))))))))))))))))))))))', 'Switch and Trigger Hybrid Folding Energy': -85.80000305175781, 'Ratio Hybrid / Switch': 1.7690722278712951, 'Trigger Complex Defect Nominal': 14.051875577288333, 'Trigger Complex Defect Normalized': 0.39032987714689815, 'Hybrid Defect Nominal': 21.400810491641455, 'Hybrid Defect Normalized': 0.16212735220940497, 'Switch Complex Defect Nominal': 32.233688323656466, 'Switch Complex Defect Normalized': 0.3357675867047549, 'Switch Defect Nominal Percentile': 96, 'Trigger Defect Nominal Percentile': 28, 'Hybrid Defect Nominal Percentile': 15, 'Algorithm Score': 199.1

TFE:  -27.46 
{'Index': 69, 'Trigger': 'AAGCAGCUUGCUGCUUUGCUGACGAGUGGCGGACGG', 'Switch Structure': '.(((((((((.......((...)).(((((((((((.(.(((((............))))).).)))))))))))....))))))..)))......', 'Switch Self-Folding Energy': -32.400001525878906, 'Switch and Trigger Hybrid Structure': '((((((((((((((((((((((((((((((((((((...(((((............))))).....((.(((.((......))))).)).......))))))))))))))))))))))))))))))))))))', 'Switch and Trigger Hybrid Folding Energy': -85.5, 'Ratio Hybrid / Switch': 2.6388887646103485, 'Trigger Complex Defect Nominal': 19.208004222997463, 'Trigger Complex Defect Normalized': 0.5335556728610407, 'Hybrid Defect Nominal': 24.00382939191121, 'Hybrid Defect Normalized': 0.1818471923629637, 'Switch Complex Defect Nominal': 23.522881096286056, 'Switch Complex Defect Normalized': 0.24503001141964642, 'Switch Defect Nominal Percentile': 54, 'Trigger Defect Nominal Percentile': 85, 'Hybrid Defect Nominal Percentile': 45, 'Algorithm Score': 190.13154550013155, 'Total

TFE:  -11.04 
{'Index': 431, 'Trigger': 'UCAGCGGGGAGGAAGGUGUUGUGGUUAAUAACCGCA', 'Switch Structure': '((.((((...)))).))........(((((((((((.(.(((((............))))).).)))))))))))......(((....))).....', 'Switch Self-Folding Energy': -33.900001525878906, 'Switch and Trigger Hybrid Structure': '((((((((((((((((((((((((((((((((((((...(((((............))))).((((.((.(((....))).)))))).........))))))))))))))))))))))))))))))))))))', 'Switch and Trigger Hybrid Folding Energy': -85.0999984741211, 'Ratio Hybrid / Switch': 2.510324325771981, 'Trigger Complex Defect Nominal': 16.043030642210372, 'Trigger Complex Defect Normalized': 0.4456397400613992, 'Hybrid Defect Nominal': 27.300445958431762, 'Hybrid Defect Normalized': 0.2068215602911497, 'Switch Complex Defect Nominal': 20.630361617611268, 'Switch Complex Defect Normalized': 0.2148996001834507, 'Switch Defect Nominal Percentile': 29, 'Trigger Defect Nominal Percentile': 58, 'Hybrid Defect Nominal Percentile': 83, 'Algorithm Score': 162.7365996814

TFE:  -23.67 
{'Index': 707, 'Trigger': 'AAUACCGGUGGCGAAGGCGGCCCCCUGGACAAAGAC', 'Switch Structure': '...(((((....(..((((((....(((((((((((.(.(((((............))))).).))))))))))).....))))))..))))))..', 'Switch Self-Folding Energy': -37.599998474121094, 'Switch and Trigger Hybrid Structure': '((((((((((((((((((((((((((((((((((((...(((((............))))).........(((...)))..(((....))).....))))))))))))))))))))))))))))))))))))', 'Switch and Trigger Hybrid Folding Energy': -86.69999694824219, 'Ratio Hybrid / Switch': 2.3058510762418005, 'Trigger Complex Defect Nominal': 13.455964625232992, 'Trigger Complex Defect Normalized': 0.3737767951453609, 'Hybrid Defect Nominal': 21.56464065026905, 'Hybrid Defect Normalized': 0.16336848977476554, 'Switch Complex Defect Nominal': 22.772482013588917, 'Switch Complex Defect Normalized': 0.23721335430821788, 'Switch Defect Nominal Percentile': 47, 'Trigger Defect Nominal Percentile': 17, 'Hybrid Defect Nominal Percentile': 16, 'Algorithm Score': 158.3697511

TFE:  -24.88 
{'Index': 783, 'Trigger': 'GAUACCCUGGUAGUCCACGCCGUAAACGAUGUCUAC', 'Switch Structure': '........((((..((.((.((..((((((((((((.(.(((((............))))).).)))))))))))).)))).))..))))......', 'Switch Self-Folding Energy': -33.79999923706055, 'Switch and Trigger Hybrid Structure': '((((((((((((((((((((((((((((((((((((...(((((............)))))..((.(((....))).))..(((....))).....))))))))))))))))))))))))))))))))))))', 'Switch and Trigger Hybrid Folding Energy': -80.5, 'Ratio Hybrid / Switch': 2.381656858492899, 'Trigger Complex Defect Nominal': 12.62797111374531, 'Trigger Complex Defect Normalized': 0.3507769753818142, 'Hybrid Defect Nominal': 23.00341321980712, 'Hybrid Defect Normalized': 0.17426828196823574, 'Switch Complex Defect Nominal': 25.469348818539302, 'Switch Complex Defect Normalized': 0.2653057168597844, 'Switch Defect Nominal Percentile': 69, 'Trigger Defect Nominal Percentile': 11, 'Hybrid Defect Nominal Percentile': 33, 'Algorithm Score': 165.01725084288375, 'Total f

TFE:  -15.51 
{'Index': 990, 'Trigger': 'CCACAGAACUUUCCAGAGAUGGAUUGGUGCCUUCGG', 'Switch Structure': '.((..(.(.(((.((((....))))(((((((((((.(.(((((............))))).).)))))))))))....))).).)..))......', 'Switch Self-Folding Energy': -27.5, 'Switch and Trigger Hybrid Structure': '((((((((((((((((((((((((((((((((((((...(((((............))))).((((.(((........)))..)))).........))))))))))))))))))))))))))))))))))))', 'Switch and Trigger Hybrid Folding Energy': -82.5999984741211, 'Ratio Hybrid / Switch': 3.003636308149858, 'Trigger Complex Defect Nominal': 17.087652672773675, 'Trigger Complex Defect Normalized': 0.47465701868815763, 'Hybrid Defect Nominal': 22.64942696582415, 'Hybrid Defect Normalized': 0.17158656792291024, 'Switch Complex Defect Nominal': 17.90339852099373, 'Switch Complex Defect Normalized': 0.18649373459368468, 'Switch Defect Nominal Percentile': 16, 'Trigger Defect Nominal Percentile': 69, 'Hybrid Defect Nominal Percentile': 27, 'Algorithm Score': 157.0518574478433, 'Total f

TFE:  -24.97 
{'Index': 1168, 'Trigger': 'AGGAAGGUGGGGAUGACGUCAAGUCAUCAUGGCCCU', 'Switch Structure': '(((.....((((((.....))))))(((((((((((.(.(((((............))))).).)))))))))))..))).(((....))).....', 'Switch Self-Folding Energy': -36.099998474121094, 'Switch and Trigger Hybrid Structure': '((((((((((((((((((((((((((((((((((((...(((((............))))).......((((....)))).(((....))).....))))))))))))))))))))))))))))))))))))', 'Switch and Trigger Hybrid Folding Energy': -85.80000305175781, 'Ratio Hybrid / Switch': 2.3767314869352427, 'Trigger Complex Defect Nominal': 20.125562821437917, 'Trigger Complex Defect Normalized': 0.5590434117066088, 'Hybrid Defect Nominal': 23.93196090015136, 'Hybrid Defect Normalized': 0.18130273409205575, 'Switch Complex Defect Nominal': 20.56568715302494, 'Switch Complex Defect Normalized': 0.21422590784400977, 'Switch Defect Nominal Percentile': 28, 'Trigger Defect Nominal Percentile': 90, 'Hybrid Defect Nominal Percentile': 44, 'Algorithm Score': 182.8905627

In [149]:
for i in new_struct:
    new_struct[i]["AVG off target binding energy"] = numpy.mean([new_struct[i]["Total free energy of binding W/ ecoli"], new_struct[i]["Total free energy of binding W/ sboydii"], new_struct[i]["Total free energy of binding W/ sdysenteriae"]])
    new_struct[i]["s16 vs related"] = new_struct[i]["Total free energy of binding W/ salmonella_16s_rna"] - new_struct[i]["AVG off target binding energy"]

In [158]:
print(new_struct)

{'UAGGCCUGCCGCCAGCGUUCAAUCUGAGCCAUGAUCGGACUUUAGAACAGAGGAGAUAAAGAUGGAUCAUGGCUCAACCUGGCGGCAGCGCAAAAG': {'Index': 7, 'Trigger': 'GAUCAUGGCUCAGAUUGAACGCUGGCGGCAGGCCUA', 'Switch Structure': '...((((((((((((.((......((((((((((((.(.(((((............))))).).)))))))))))))))))))))))).)).....', 'Switch Self-Folding Energy': -48.5, 'Switch and Trigger Hybrid Structure': '((((((((((((((((((((((((((((((((((((...........(((..(((.....((....))....)))...)))(((....))).....))))))))))))))))))))))))))))))))))))', 'Switch and Trigger Hybrid Folding Energy': -85.80000305175781, 'Ratio Hybrid / Switch': 1.7690722278712951, 'Trigger Complex Defect Nominal': 14.051875577288333, 'Trigger Complex Defect Normalized': 0.39032987714689815, 'Hybrid Defect Nominal': 21.400810491641455, 'Hybrid Defect Normalized': 0.16212735220940497, 'Switch Complex Defect Nominal': 32.233688323656466, 'Switch Complex Defect Normalized': 0.3357675867047549, 'Switch Defect Nominal Percentile': 96, 'Trigger Defect Nominal Percentile': 28

In [163]:
avg_sorted = sorted(new_struct, key=lambda x: (new_struct[x]["s16 vs related"]))
for i in avg_sorted:
    print(i, new_struct[i])

AAGGCACCAAUCCAUCUCUGGAAAGUUCUGUGGAUGGGACUUUAGAACAGAGGAGAUAAAGAUGCAUCCACAGAAAACCUGGCGGCAGCGCAAAAG {'Index': 987, 'Trigger': 'CAUCCACAGAACUUUCCAGAGAUGGAUUGGUGCCUU', 'Switch Structure': '.(((......((((....))))...(((((((((((.(.(((((............))))).).)))))))))))..))).(((....))).....', 'Switch Self-Folding Energy': -27.299999237060547, 'Switch and Trigger Hybrid Structure': '((((((((((((((((((((((((((((((((((((((((((((............))))).....))).(((.....)))(((....))).....))))))))))))))))))))))))))))))))))))', 'Switch and Trigger Hybrid Folding Energy': -78.30000305175781, 'Ratio Hybrid / Switch': 2.8681320600721216, 'Switch Complex Defect Nominal': 16.976524305003714, 'Switch Complex Defect Normalized': 0.1768387948437887, 'Hybrid Defect Nominal': 25.195379985324955, 'Hybrid Defect Normalized': 0.1908740907979163, 'Trigger Complex Defect Nominal': 15.162359550261897, 'Trigger Complex Defect Normalized': 0.42117665417394157, 'Switch Defect Nominal Percentile': 10, 'Trigger Defect Nominal Perc

In [164]:
for i in new_struct:
    df = pd.DataFrame(new_struct, index=new_struct[i].keys())
    df.to_excel("folding_data.xlsx")

Exception ignored in: <function ZipFile.__del__ at 0x7f4334ce91f0>
Traceback (most recent call last):
  File "/root/miniconda3/lib/python3.9/zipfile.py", line 1816, in __del__
    self.close()
  File "/root/miniconda3/lib/python3.9/zipfile.py", line 1833, in close
    self.fp.seek(self.start_dir)
ValueError: seek of closed file
